In [1]:
!pip install facenet-pytorch  # fornisce modelli pre-addestrati PyTorch per compiti di riconoscimento facciale
!pip install Pillow # aggiunge il supporto per l'apertura, la manipolazione e il salvataggio di molti diversi formati di file immagine.

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [3]:
%cd /content/drive/Shareddrives/AI4CYBSEC/face_dataset/

/content/drive/Shareddrives/AI4CYBSEC/face_dataset


In [ ]:
MOVE_IMAGES = False

In [ ]:
if MOVE_IMAGES:
  import os
  import shutil
  from tqdm import tqdm

  def rename_and_copy_images(src_dir, dst_dir):
      # Crea la directory di destinazione se non esiste
      if not os.path.exists(dst_dir):
          os.makedirs(dst_dir)

      # Itera attraverso tutte le sottocartelle della directory sorgente
      for subdir, _, files in tqdm(os.walk(src_dir), desc='Processing folder'):
          # Ottieni il nome della sottodirectory
          relative_path = os.path.relpath(subdir, src_dir)
          if relative_path == '.':
              continue

          for file in files:
              # Costruisci il percorso completo del file sorgente
              src_file_path = os.path.join(subdir, file)
              # Costruisci il nuovo nome del file
              new_file_name = f"{relative_path}_{file}"
              # Costruisci il percorso completo del file di destinazione
              dst_file_path = os.path.join(dst_dir, new_file_name)
              # Copia il file rinominato nella directory di destinazione
              shutil.copy2(src_file_path, dst_file_path)

  src_directory = './train_detector_set'
  dst_directory = './train_detector_shuffle/0'
  rename_and_copy_images(src_directory, dst_directory)

  src_directory = './validation_detector_set'
  dst_directory = './train_detector_shuffle/0'
  rename_and_copy_images(src_directory, dst_directory)

## CROP IMAGES

In [ ]:
PERFORM_CROP = False

In [ ]:
if PERFORM_CROP:
  from facenet_pytorch import MTCNN
  import cv2
  from PIL import Image
  import numpy as np
  from matplotlib import pyplot as plt
  from tqdm.notebook import tqdm
  import torch

  # Create face detector
  device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
  print('Running on device: {}'.format(device))
  mtcnn = MTCNN(select_largest=False, device=device, image_size=160)

  training_set_path = './train_detector_shuffle/0'

  # List of files in the dataset
  import os
  root_dir = training_set_path
  file_list = []
  for root, dirs, files in os.walk(root_dir):
      for file in files:
          file_list.append(os.path.join(root, file))

  import os

  # Define the root folder and dataset name
  root_MTCNN_dataset = "/content/drive/Shareddrives/AI4CYBSEC/face_dataset/train_detector_shuffle"
  name_dataset = "0_MTCNN"

  # Combine the root folder and dataset name to create the full path
  dataset_path = os.path.join(root_MTCNN_dataset, name_dataset)

  # Create the folder if it doesn't exist
  if not os.path.exists(dataset_path):
      os.makedirs(dataset_path)
      print("Folder created:", dataset_path)
  else:
      print("Folder already exists.")

  for i in tqdm(range(len(file_list)), desc='Cropping images'):
    frame = Image.open(file_list[i])
    name_image = os.path.basename(file_list[i])
    path_save = os.path.join(dataset_path,name_image)
    #print(f"{i}/{len(file_list)} -- Image name : {name_image} [PATH SAVE: {path_save}]" )
    mtcnn(frame, save_path=path_save)

# Prepare Training Set for Attacks

In [1]:
import torch
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
print('Running on device: {}'.format(device))


Running on device: cuda:0


In [5]:
import os
import random
from tqdm.notebook import tqdm
import numpy as np
from PIL import Image

def get_image_files(src_dir):
    image_files = []
    count = 0
    for subdir, _, files in  os.walk(src_dir):
          for file in files:
              if file.lower().endswith(('.png', '.jpg', '.jpeg', '.gif', '.bmp')):
                  try:
                    image_files.append(np.array(Image.open(os.path.join(subdir, file))))
                    count += 1
                    #stampa il numero di immagini lette con param -r senza andarte a capo 
                    print(f"\r{count}", end="")
                    # if count == 1000:
                    #     break

                  except:
                    print(f"Error reading file: {os.path.join(subdir, file)}")
                    pass
    return image_files

def generate_random_indices(image_files, num_lists=5):
    seed = 42
    random.seed(seed)

    num_images = len(image_files)
    indices = list(range(num_images))

    # Shuffle una sola volta
    random.shuffle(indices)

    # Prendi i primi 10000 campioni
    selected_indices = indices[:10000]

    # Dividi i 10000 campioni in num_lists liste
    chunk_size = len(selected_indices) // num_lists
    random_indices_lists = [selected_indices[i*chunk_size:(i+1)*chunk_size] for i in range(num_lists)]

    return random_indices_lists


# Esempio di utilizzo
src_directory = './face_dataset/train_detector_shuffle/0_MTCNN'
image_files = get_image_files(src_directory)
random_indices_lists = generate_random_indices(image_files)

# Definire gli attacchi
attacks = ['fgsm', 'bim', 'pgd', 'df', 'cw']
sample_for_attack = {}

# Creare le chiavi nel dizionario
for i, indices in enumerate(random_indices_lists):
    half_index = len(indices) // 2
    untargeted_indices = indices[:half_index]
    targeted_indices = indices[half_index:]

    sample_for_attack[attacks[i]] = {
        'untargeted': untargeted_indices,
        'targeted': targeted_indices
    }

# Stampa il dizionario dei campioni per attacco
for attack, indices in sample_for_attack.items():
    print(f"Attack: {attack}")
    print(f"  Untargeted: {indices['untargeted']}")
    print(f"  Len Untargeted: {len(indices['untargeted'])}")
    print(f"  Targeted: {indices['targeted']}")
    print(f"  Targeted: {len(indices['targeted'])}")

9939Error reading file: ./face_dataset/train_detector_shuffle/0_MTCNN\n008229_0565_01.jpg
10001Attack: fgsm
  Untargeted: [3771, 6672, 7261, 760, 3779, 1772, 7509, 2679, 2305, 9215, 3625, 4236, 9005, 5924, 3093, 7590, 4736, 4366, 4056, 4178, 1287, 8343, 4623, 2066, 9099, 5950, 1547, 7599, 313, 8321, 3916, 5943, 3162, 2010, 7296, 4163, 8426, 4080, 4026, 2345, 324, 2733, 704, 5877, 7875, 1651, 585, 4625, 3939, 1603, 5581, 5459, 4165, 7796, 5112, 6700, 4531, 9223, 1241, 5250, 5045, 147, 2263, 5451, 5346, 4259, 5360, 1721, 3229, 8478, 8262, 3462, 9136, 1995, 3286, 3463, 8498, 7617, 7675, 6028, 7190, 8589, 5136, 4958, 7093, 3035, 6293, 6488, 1185, 516, 4749, 1062, 2919, 1400, 8487, 8310, 3002, 5002, 3205, 5880, 7142, 5857, 6401, 4172, 2059, 5616, 6296, 8168, 6602, 5069, 526, 143, 9710, 4343, 709, 477, 6080, 2966, 5471, 3015, 6742, 6231, 7457, 8858, 3327, 6975, 640, 1161, 6378, 6245, 8493, 959, 6383, 4447, 3640, 281, 6944, 9318, 4423, 7983, 1243, 3535, 3422, 4909, 9247, 6656, 4025, 6289, 789

In [4]:
for attack, indices in sample_for_attack.items():
    print(f"Attack: {attack}")
    print(f"  Untargeted: {indices['untargeted']}")
    print(f"  Len Untargeted: {len(indices['untargeted'])}")
    print(f"  Targeted: {indices['targeted']}")
    print(f"  Targeted: {len(indices['targeted'])}")

Attack: df
  Untargeted: [3771, 6672, 7261, 760, 3779, 1772, 7509, 2679, 2305, 9215, 3625, 4236, 9005, 5924, 3093, 7590, 4736, 4366, 4056, 4178, 1287, 8343, 4623, 2066, 9099, 5950, 1547, 7599, 313, 8321, 3916, 5943, 3162, 2010, 7296, 4163, 8426, 4080, 4026, 2345, 324, 2733, 704, 5877, 7875, 1651, 585, 4625, 3939, 1603, 5581, 5459, 4165, 7796, 5112, 6700, 4531, 9223, 1241, 5250, 5045, 147, 2263, 5451, 5346, 4259, 5360, 1721, 3229, 8478, 8262, 3462, 9136, 1995, 3286, 3463, 8498, 7617, 7675, 6028, 7190, 8589, 5136, 4958, 7093, 3035, 6293, 6488, 1185, 516, 4749, 1062, 2919, 1400, 8487, 8310, 3002, 5002, 3205, 5880, 7142, 5857, 6401, 4172, 2059, 5616, 6296, 8168, 6602, 5069, 526, 143, 9710, 4343, 709, 477, 6080, 2966, 5471, 3015, 6742, 6231, 7457, 8858, 3327, 6975, 640, 1161, 6378, 6245, 8493, 959, 6383, 4447, 3640, 281, 6944, 9318, 4423, 7983, 1243, 3535, 3422, 4909, 9247, 6656, 4025, 6289, 7896, 4443, 3859, 4933, 5034, 2745, 361, 9530, 7871, 7294, 9475, 7005, 9805, 5444, 169, 82, 9697, 57

In [3]:
print(image_files[sample_for_attack['df']['untargeted'][0]])
print(image_files[sample_for_attack['df']['untargeted'][0]].shape)

[[[187 118  76]
  [193 124  82]
  [199 132  89]
  ...
  [153 103  80]
  [152 106  83]
  [149 104  81]]

 [[187 118  76]
  [187 118  76]
  [187 120  77]
  ...
  [143  93  70]
  [143  97  74]
  [141  95  72]]

 [[191 122  80]
  [186 117  75]
  [181 114  71]
  ...
  [131  79  57]
  [134  83  62]
  [132  84  62]]

 ...

 [[178  93  64]
  [178  93  64]
  [179  94  65]
  ...
  [119  73  58]
  [120  74  59]
  [120  74  59]]

 [[182  97  68]
  [182  97  68]
  [183  98  69]
  ...
  [119  73  58]
  [119  73  58]
  [120  74  59]]

 [[186 101  72]
  [186 101  72]
  [186 101  72]
  ...
  [119  73  58]
  [120  74  59]
  [120  74  59]]]
(160, 160, 3)


### sample_for_attack è un dizionario che contiene come chiave l'attacco e come valori delle liste di indici tramite cui è possibile accedere a image_files per recuperare le immagini corrispondenti. Tramite ulteriore chiave "unatageted" o "targeted" posso accedere ai campioni per gli attacchi untargeted o targeted.



# LOAD MODEL

In [3]:
# utilizzo la libreria facenet_pytorch per caricare il modello InceptionResnetV1 preaddestrato sul dataset VGGFace2 e abilitare la classificazione.
from facenet_pytorch import InceptionResnetV1, MTCNN
import torch

device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
print('Running on device: {}'.format(device))

resnet = InceptionResnetV1(pretrained='vggface2', device=device).eval()
resnet.classify = True
resnet = resnet.to(device)

Running on device: cuda:0


# GENERATE ATTACKS

In [ ]:
!pip install adversarial-robustness-toolbox[all]

In [10]:

import art

In [11]:
from art.estimators.classification import PyTorchClassifier

from torch import nn, optim
import torchvision.transforms as transforms

import numpy as np

input_shape = (3,160,160)
nb_classes = 8631
loss = nn.CrossEntropyLoss()    # Triplett loss = nn.TripletMarginLoss()
optimizer = optim.Adam(resnet.parameters())
classifier = PyTorchClassifier(model=resnet, loss=loss, input_shape=input_shape, nb_classes=nb_classes, optimizer=optimizer, clip_values=(0, 1))

## FGSM

In [ ]:
from art.attacks.evasion import FastGradientMethod


In [ ]:
images_list = []
for idx in tqdm(sample_for_attack['fgsm']['untargeted'], desc="Preparing dataset"):
    image = np.transpose(image_files[idx], (2, 0, 1))
    image = image / 255.0
    image = image.astype(np.float32)
    images_list.append(image)

Preparing dataset: 100%|██████████| 1000/1000 [00:00<00:00, 3487.51it/s]

1000
(3, 160, 160)


In [ ]:
from tqdm import tqdm
import numpy as np
from PIL import Image
import matplotlib.pyplot as plt

epsilon = 0.1
targeted = False
fgsm_untargeted_attacker = FastGradientMethod(estimator=classifier, eps=epsilon, targeted=targeted)

eps_range = [0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]
attack_name = 'FGSM_untargeted'

batch_size = len(images_list) // len(eps_range)

for batch_idx in range(0, len(images_list)-1, batch_size):
    # print(f"Batch starting at index {batch_idx}")

    # Determine epsilon index for this batch
    eps_index = batch_idx // batch_size
    current_eps = eps_range[eps_index]

    # Set epsilon for the attacker
    fgsm_untargeted_attacker.set_params(**{'eps': current_eps})
    # print(current_eps)

    for idx in tqdm(range(batch_idx, min(batch_idx + batch_size, len(images_list))), desc=f'Processing FGSM untargeted with eps: {current_eps}'):
        img = images_list[idx]
        img = np.expand_dims(img, axis=0)
        x_train_adv = fgsm_untargeted_attacker.generate(img)
        x_train_adv = x_train_adv.squeeze(0)
        x_train_adv = (x_train_adv*255.0).astype(np.uint8)

        # Create PIL image
        image = Image.fromarray(np.transpose(x_train_adv, (1, 2, 0)))

        # # Plot dell'immagine
        # plt.imshow(image)
        # plt.axis('off')  # Rimuove gli assi del plot

        # # Mostra il plot
        # plt.show()

        # Crea la directory se non esiste
        directory = f"/content/drive/Shareddrives/AI4CYBSEC/face_dataset/adversarial_samples/{attack_name}"
        if not os.path.exists(directory):
          os.makedirs(directory)

        # Save the image
        image.save(f"/content/drive/Shareddrives/AI4CYBSEC/face_dataset/adversarial_samples/{attack_name}/image_eps_{current_eps}_{idx}.jpg")

print("Adversarial images generation with FGSM untargeted completed.")

Processing FGSM untargeted: 100%|██████████| 111/111 [01:15<00:00,  1.48it/s]

Adversarial images generation with FGSM untargeted completed.


In [ ]:
images_list = []
for idx in tqdm(sample_for_attack['fgsm']['targeted'], desc="Preparing dataset"):
    image = np.transpose(image_files[idx], (2, 0, 1))
    image = image / 255.0
    image = image.astype(np.float32)
    images_list.append(image)

Preparing dataset: 100%|██████████| 1000/1000 [00:00<00:00, 4638.90it/s]


In [ ]:
from tqdm import tqdm
import numpy as np
from PIL import Image
import matplotlib.pyplot as plt
import tensorflow as tf

epsilon = 0.1
targeted=True
fgsm_targeted_attacker = FastGradientMethod(estimator=classifier, eps=epsilon, targeted=targeted)
target_class = 0

eps_range = [0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]
attack_name = 'FGSM_targeted'

targeted_label = np.array(target_class)
one_hot_bob_targeted_label = np.expand_dims(tf.keras.utils.to_categorical(targeted_label, num_classes=nb_classes), axis=0)

batch_size = len(images_list) // len(eps_range)

for batch_idx in range(0, len(images_list)-1, batch_size):
    # print(f"Batch starting at index {batch_idx}")

    # Determine epsilon index for this batch
    eps_index = batch_idx // batch_size
    current_eps = eps_range[eps_index]

    # Set epsilon for the attacker
    fgsm_targeted_attacker.set_params(**{'eps': current_eps})
    # print(current_eps)

    for idx in tqdm(range(batch_idx, min(batch_idx + batch_size, len(images_list))), desc=f'Processing FGSM targeted with eps: {current_eps}'):
        img = images_list[idx]
        img = np.expand_dims(img, axis=0)
        x_train_adv = fgsm_targeted_attacker.generate(img, one_hot_bob_targeted_label)
        x_train_adv = x_train_adv.squeeze(0)
        x_train_adv = (x_train_adv*255.0).astype(np.uint8)

        # Create PIL image
        image = Image.fromarray(np.transpose(x_train_adv, (1, 2, 0)))

        # # Plot dell'immagine
        # plt.imshow(image)
        # plt.axis('off')  # Rimuove gli assi del plot

        # # Mostra il plot
        # plt.show()

        # Crea la directory se non esiste
        directory = f"/content/drive/Shareddrives/AI4CYBSEC/face_dataset/adversarial_samples/{attack_name}"
        if not os.path.exists(directory):
          os.makedirs(directory)

        # Save the image
        image.save(f"/content/drive/Shareddrives/AI4CYBSEC/face_dataset/adversarial_samples/{attack_name}/image_eps_{current_eps}_{idx}.jpg")

print("Adversarial images generation with FGSM targeted completed.")

Processing FGSM targeted with eps: 0.9: 100%|██████████| 111/111 [00:50<00:00,  2.18it/s]

Adversarial images generation with FGSM targeted completed.


## BIM


In [ ]:
from art.attacks.evasion import BasicIterativeMethod

In [ ]:
images_list = []
for idx in tqdm(sample_for_attack['bim']['untargeted'], desc="Preparing dataset"):
    image = np.transpose(image_files[idx], (2, 0, 1))
    image = image / 255.0
    image = image.astype(np.float32)
    images_list.append(image)

Preparing dataset: 100%|██████████| 1000/1000 [00:00<00:00, 2514.30it/s]


In [ ]:
#%rm -r './adversarial_samples/BIM_untargeted'

In [ ]:
from tqdm import tqdm
import numpy as np
from PIL import Image
import matplotlib.pyplot as plt
import math
from math import ceil

epsilon = 0.1
epsilon_step = 0.1
max_iter = 5
targeted = False
bim_untargeted_attacker = BasicIterativeMethod(estimator=classifier, eps=epsilon, eps_step=epsilon_step, max_iter=max_iter, targeted=targeted, verbose=False)

eps_range = [0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]
max_iter_range = [2, 5, 10]
attack_name = 'BIM_untargeted'

images_list_max_iter = []
max_iter_range_len = len(max_iter_range)
offset_max_iter = len(images_list)//max_iter_range_len

for jjeee in range(max_iter_range_len):
  if len(images_list) - (jjeee*offset_max_iter+offset_max_iter) < offset_max_iter:
    end_slice = len(images_list)
  else:
    end_slice = jjeee*offset_max_iter+offset_max_iter
  images_list_max_iter.append(images_list[jjeee*offset_max_iter:end_slice])


for jjeee in range(max_iter_range_len):
  batch_size = ceil(len(images_list_max_iter[jjeee]) / len(eps_range))

  for batch_idx in range(0, len(images_list_max_iter[jjeee])-1, batch_size):

      # Determine epsilon index for this batch
      eps_index = batch_idx // batch_size
      current_eps = eps_range[eps_index]

      # Set epsilon for the attacker
      bim_untargeted_attacker.set_params(**{'eps': current_eps, 'eps_step':current_eps/10, 'max_iter':max_iter_range[jjeee]})
      # print(current_eps)

      for idx in tqdm(range(batch_idx, min(batch_idx + batch_size, len(images_list))), desc=f'Processing BIM untargeted with eps: {current_eps}'):
          img = images_list[idx]
          img = np.expand_dims(img, axis=0)
          x_train_adv = bim_untargeted_attacker.generate(img)
          x_train_adv = x_train_adv.squeeze(0)
          x_train_adv = (x_train_adv*255.0).astype(np.uint8)

          # # Create PIL image
          image = Image.fromarray(np.transpose(x_train_adv, (1, 2, 0)))

          # # Plot dell'immagine
          # plt.imshow(image)
          # plt.axis('off')  # Rimuove gli assi del plot

          # # Mostra il plot
          # plt.show()

          # Crea la directory se non esiste
          directory = f"/content/drive/Shareddrives/AI4CYBSEC/face_dataset/adversarial_samples/{attack_name}"
          if not os.path.exists(directory):
            os.makedirs(directory)

          # Save the image
          image.save(f"/content/drive/Shareddrives/AI4CYBSEC/face_dataset/adversarial_samples/{attack_name}/image_max_iter_{max_iter_range[jjeee]}_eps_{current_eps}_{idx}.jpg")

print("Adversarial images generation with BIM untargeted completed.")

Processing BIM untargeted with eps: 0.9: 100%|██████████| 38/38 [02:43<00:00,  4.31s/it]

Adversarial images generation with BIM untargeted completed.


In [ ]:
images_list = []
for idx in tqdm(sample_for_attack['bim']['targeted'], desc="Preparing dataset"):
    image = np.transpose(image_files[idx], (2, 0, 1))
    image = image / 255.0
    image = image.astype(np.float32)
    images_list.append(image)

Preparing dataset: 100%|██████████| 1000/1000 [00:00<00:00, 1576.90it/s]


In [ ]:
from tqdm import tqdm
import numpy as np
from PIL import Image
import matplotlib.pyplot as plt
import math
from math import ceil

epsilon = 0.1
epsilon_step = 0.1
max_iter = 5
targeted = True
bim_targeted_attacker = BasicIterativeMethod(estimator=classifier, eps=epsilon, eps_step=epsilon_step, max_iter=max_iter, targeted=targeted, verbose=True)
target_class = 0

targeted_label = np.array(target_class)
one_hot_bob_targeted_label = np.expand_dims(tf.keras.utils.to_categorical(targeted_label, num_classes=nb_classes), axis=0)


eps_range = [0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]
max_iter_range = [2, 5, 10]
attack_name = 'BIM_targeted'

images_list_max_iter = []
max_iter_range_len = len(max_iter_range)
offset_max_iter = len(images_list)//max_iter_range_len

for jjeee in range(max_iter_range_len):
  if len(images_list) - (jjeee*offset_max_iter+offset_max_iter) < offset_max_iter:
    end_slice = len(images_list)
  else:
    end_slice = jjeee*offset_max_iter+offset_max_iter
  images_list_max_iter.append(images_list[jjeee*offset_max_iter:end_slice])


for jjeee in range(max_iter_range_len):
  batch_size = ceil(len(images_list_max_iter[jjeee]) / len(eps_range))

  for batch_idx in range(0, len(images_list_max_iter[jjeee])-1, batch_size):

      # Determine epsilon index for this batch
      eps_index = batch_idx // batch_size
      current_eps = eps_range[eps_index]

      # Set epsilon for the attacker
      bim_untargeted_attacker.set_params(**{'eps': current_eps, 'eps_step':current_eps/10, 'max_iter':max_iter_range[jjeee]})
      # print(current_eps)

      for idx in tqdm(range(batch_idx, min(batch_idx + batch_size, len(images_list))), desc=f'Processing BIM untargeted with eps: {current_eps}'):
          img = images_list[idx]
          img = np.expand_dims(img, axis=0)
          x_train_adv = bim_targeted_attacker.generate(img, one_hot_bob_targeted_label)
          x_train_adv = x_train_adv.squeeze(0)
          x_train_adv = (x_train_adv*255.0).astype(np.uint8)

          # # Create PIL image
          image = Image.fromarray(np.transpose(x_train_adv, (1, 2, 0)))

          # # Plot dell'immagine
          # plt.imshow(image)
          # plt.axis('off')  # Rimuove gli assi del plot

          # # Mostra il plot
          # plt.show()

          # Crea la directory se non esiste
          directory = f"/content/drive/Shareddrives/AI4CYBSEC/face_dataset/adversarial_samples/{attack_name}"
          if not os.path.exists(directory):
            os.makedirs(directory)

          # Save the image
          image.save(f"/content/drive/Shareddrives/AI4CYBSEC/face_dataset/adversarial_samples/{attack_name}/image_max_iter_{max_iter_range[jjeee]}_eps_{current_eps}_{idx}.jpg")

print("Adversarial images generation with BIM targeted completed.")

Processing BIM untargeted with eps: 0.1:   0%|          | 0/37 [00:00<?, ?it/s]

PGD - Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Processing BIM untargeted with eps: 0.1:   3%|▎         | 1/37 [00:01<01:10,  1.97s/it]

PGD - Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Processing BIM untargeted with eps: 0.1:   5%|▌         | 2/37 [00:03<01:08,  1.94s/it]

...

PGD - Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Processing BIM untargeted with eps: 0.9:  97%|█████████▋| 37/38 [01:31<00:02,  2.59s/it]

PGD - Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Processing BIM untargeted with eps: 0.9: 100%|██████████| 38/38 [01:33<00:00,  2.47s/it]

Adversarial images generation with BIM targeted completed.


## PGD

In [25]:
from art.attacks.evasion import ProjectedGradientDescentPyTorch
from math import ceil


In [26]:
images_list = []
for idx in tqdm(sample_for_attack['pgd']['untargeted'], desc="Preparing dataset"):
    image = np.transpose(image_files[idx], (2, 0, 1))
    image = image / 255.0
    image = image.astype(np.float32)
    images_list.append(image)

Preparing dataset:   0%|          | 0/1000 [00:00<?, ?it/s]

In [27]:

targeted = False
epsilon = [0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]
# già ho fatto 2 poi mi è crushato
max_iters = [2, 5, 10]
#max_iters = [ 5, 10, 20]
num_random_init = 5 # for reproducibility
target_class = None
attack_name = 'PGD_untargeted'

images_list_max_iter = []
max_iters_len = len(max_iters)
offset_max_iter = len(images_list)//max_iters_len

for curr_iter_idx in range(max_iters_len):
  if len(images_list) - (curr_iter_idx*offset_max_iter+offset_max_iter) < offset_max_iter:
    end_slice = len(images_list)
  else:
    end_slice = curr_iter_idx*offset_max_iter+offset_max_iter
  images_list_max_iter.append(images_list[curr_iter_idx*offset_max_iter:end_slice])


for curr_iter_idx in range(max_iters_len):
  batch_size = ceil(len(images_list_max_iter[curr_iter_idx]) / len(epsilon))

  for batch_idx in range(0, len(images_list_max_iter[curr_iter_idx])-1, batch_size):
      # Determine epsilon index for this batch
      eps_index = batch_idx // batch_size
      current_eps = epsilon[eps_index]

      # Set epsilon for the attacker
      pgd_untargeted_attacker = ProjectedGradientDescentPyTorch(estimator=classifier, eps=current_eps, eps_step=current_eps/10, max_iter=max_iters[curr_iter_idx], targeted=targeted, num_random_init=num_random_init, batch_size=1, verbose=False)

      for idx in tqdm(range(batch_idx, min(batch_idx + batch_size, len(images_list))), desc=f'Processing PGD untargeted with eps: {current_eps} and max_iter: {max_iters[curr_iter_idx]}'):
          img = images_list[idx]
          img = np.expand_dims(img, axis=0)
          x_train_adv = pgd_untargeted_attacker.generate(img)
          x_train_adv = x_train_adv.squeeze(0)
          x_train_adv = (x_train_adv*255.0).astype(np.uint8)

          # # Create PIL image
          image = Image.fromarray(np.transpose(x_train_adv, (1, 2, 0)))
          # Crea la directory se non esiste
          directory = f"./face_dataset/adversarial_samples/{attack_name}"
          if not os.path.exists(directory):
            os.makedirs(directory)

          # Save the image
          image.save(f"./face_dataset/adversarial_samples/{attack_name}/image_max_iter_{max_iters[curr_iter_idx]}_eps_{current_eps}_{idx}.jpg")

Processing PGD untargeted with eps: 0.1 and max_iter: 2:   0%|          | 0/37 [00:00<?, ?it/s]

Processing PGD untargeted with eps: 0.2 and max_iter: 2:   0%|          | 0/37 [00:00<?, ?it/s]

Processing PGD untargeted with eps: 0.3 and max_iter: 2:   0%|          | 0/37 [00:00<?, ?it/s]

Processing PGD untargeted with eps: 0.4 and max_iter: 2:   0%|          | 0/37 [00:00<?, ?it/s]

Processing PGD untargeted with eps: 0.5 and max_iter: 2:   0%|          | 0/37 [00:00<?, ?it/s]

...

Processing PGD untargeted with eps: 0.5 and max_iter: 10:   0%|          | 0/38 [00:00<?, ?it/s]

Processing PGD untargeted with eps: 0.6 and max_iter: 10:   0%|          | 0/38 [00:00<?, ?it/s]

Processing PGD untargeted with eps: 0.7 and max_iter: 10:   0%|          | 0/38 [00:00<?, ?it/s]

Processing PGD untargeted with eps: 0.8 and max_iter: 10:   0%|          | 0/38 [00:00<?, ?it/s]

Processing PGD untargeted with eps: 0.9 and max_iter: 10:   0%|          | 0/38 [00:00<?, ?it/s]

In [28]:
images_list = []
for idx in tqdm(sample_for_attack['pgd']['targeted'], desc="Preparing dataset"):
    image = np.transpose(image_files[idx], (2, 0, 1))
    image = image / 255.0
    image = image.astype(np.float32)
    images_list.append(image)

Preparing dataset:   0%|          | 0/1000 [00:00<?, ?it/s]

In [29]:

targeted = True
epsilon = [0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]
# già ho fatto 2 poi mi è crushato
max_iters = [2, 5, 10]
#max_iters = [ 5, 10, 20]
num_random_init = 5 # for reproducibility
target_class = None
attack_name = 'PGD_targeted'


target_class = 0 ## n000002 id_label_dict["n000002"] = 0 --> OK THE SAME FOR NN1
one_hot_bob_targeted_label = np.zeros((1, 8631))
one_hot_bob_targeted_label[:, target_class] = 1


images_list_max_iter = []
max_iters_len = len(max_iters)
offset_max_iter = len(images_list)//max_iters_len

for curr_iter_idx in range(max_iters_len):
  if len(images_list) - (curr_iter_idx*offset_max_iter+offset_max_iter) < offset_max_iter:
    end_slice = len(images_list)
  else:
    end_slice = curr_iter_idx*offset_max_iter+offset_max_iter
  images_list_max_iter.append(images_list[curr_iter_idx*offset_max_iter:end_slice])


for curr_iter_idx in range(max_iters_len):
  batch_size = ceil(len(images_list_max_iter[curr_iter_idx]) / len(epsilon))

  for batch_idx in range(0, len(images_list_max_iter[curr_iter_idx])-1, batch_size):
      # Determine epsilon index for this batch
      eps_index = batch_idx // batch_size
      current_eps = epsilon[eps_index]

      # Set epsilon for the attacker
      pgd_targeted_attacker = ProjectedGradientDescentPyTorch(estimator=classifier, eps=current_eps, eps_step=current_eps/10, max_iter=max_iters[curr_iter_idx], targeted=targeted, num_random_init=num_random_init, batch_size=1, verbose=False)

      for idx in tqdm(range(batch_idx, min(batch_idx + batch_size, len(images_list))), desc=f'Processing PGD untargeted with eps: {current_eps} and max_iter: {max_iters[curr_iter_idx]}'):
          img = images_list[idx]
          img = np.expand_dims(img, axis=0)
          x_train_adv = pgd_targeted_attacker.generate(img, one_hot_bob_targeted_label)
          x_train_adv = x_train_adv.squeeze(0)
          x_train_adv = (x_train_adv*255.0).astype(np.uint8)

          # # Create PIL image
          image = Image.fromarray(np.transpose(x_train_adv, (1, 2, 0)))
          # Crea la directory se non esiste
          directory = f"./face_dataset/adversarial_samples/{attack_name}"
          if not os.path.exists(directory):
            os.makedirs(directory)

          # Save the image
          image.save(f"./face_dataset/adversarial_samples/{attack_name}/image_max_iter_{max_iters[curr_iter_idx]}_eps_{current_eps}_{idx}.jpg")

Processing PGD untargeted with eps: 0.1 and max_iter: 2:   0%|          | 0/37 [00:00<?, ?it/s]

Processing PGD untargeted with eps: 0.2 and max_iter: 2:   0%|          | 0/37 [00:00<?, ?it/s]

Processing PGD untargeted with eps: 0.3 and max_iter: 2:   0%|          | 0/37 [00:00<?, ?it/s]

Processing PGD untargeted with eps: 0.4 and max_iter: 2:   0%|          | 0/37 [00:00<?, ?it/s]

Processing PGD untargeted with eps: 0.5 and max_iter: 2:   0%|          | 0/37 [00:00<?, ?it/s]

...

Processing PGD untargeted with eps: 0.5 and max_iter: 10:   0%|          | 0/38 [00:00<?, ?it/s]

Processing PGD untargeted with eps: 0.6 and max_iter: 10:   0%|          | 0/38 [00:00<?, ?it/s]

Processing PGD untargeted with eps: 0.7 and max_iter: 10:   0%|          | 0/38 [00:00<?, ?it/s]

Processing PGD untargeted with eps: 0.8 and max_iter: 10:   0%|          | 0/38 [00:00<?, ?it/s]

Processing PGD untargeted with eps: 0.9 and max_iter: 10:   0%|          | 0/38 [00:00<?, ?it/s]

## Deepfool

In [4]:
from art.attacks.evasion import DeepFool

In [6]:
import os
from tqdm import tqdm
import numpy as np
from PIL import Image

def get_image_files(src_dir):
    image_files = []
    count = 0
    for subdir, _, files in  os.walk(src_dir):
          for file in files:
              if file.lower().endswith(('.png', '.jpg', '.jpeg', '.gif', '.bmp')):
                  try:
                    image_files.append(np.array(Image.open(os.path.join(subdir, file))))
                    count += 1
                    #stampa il numero di immagini lette con param -r senza andarte a capo 
                    print(f"\r{count}", end="")
                    # if count == 1000:
                    #     break

                  except:
                    print(f"Error reading file: {os.path.join(subdir, file)}")
                    pass
    return image_files
src_dir = 'G:\Drive condivisi\AI4CYBSEC\\face_dataset\\test_set_MTCNN'
image_files = get_image_files(src_dir)

998

In [29]:
print(image_files[0].shape)

(160, 160, 3)


In [7]:
images_list = []
for idx in range(len(image_files)):
    print(idx)
    image = np.transpose(image_files[idx], (2, 0, 1))
    image = image / 255.0
    image = image.astype(np.float32)
    images_list.append(image)
print(len(images_list))

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [11]:
images_list = []
for idx in tqdm(sample_for_attack['df']['untargeted'], desc="Preparing dataset"):
    image = np.transpose(image_files[idx], (2, 0, 1))
    image = image / 255.0
    image = image.astype(np.float32)
    images_list.append(image)
for idx in tqdm(sample_for_attack['df']['targeted'], desc="Preparing dataset"):
    image = np.transpose(image_files[idx], (2, 0, 1))
    image = image / 255.0
    image = image.astype(np.float32)
    images_list.append(image)
for idx in tqdm(sample_for_attack['pgd']['untargeted'], desc="Preparing dataset"):
    image = np.transpose(image_files[idx], (2, 0, 1))
    image = image / 255.0
    image = image.astype(np.float32)
    images_list.append(image)
for idx in tqdm(sample_for_attack['pgd']['targeted'], desc="Preparing dataset"):
    image = np.transpose(image_files[idx], (2, 0, 1))
    image = image / 255.0
    image = image.astype(np.float32)
    images_list.append(image)
for idx in tqdm(sample_for_attack['bim']['untargeted'], desc="Preparing dataset"):
    image = np.transpose(image_files[idx], (2, 0, 1))
    image = image / 255.0
    image = image.astype(np.float32)
    images_list.append(image)


print(len(images_list))

Preparing dataset:   0%|          | 0/1000 [00:00<?, ?it/s]

Preparing dataset:   0%|          | 0/1000 [00:00<?, ?it/s]

Preparing dataset:   0%|          | 0/1000 [00:00<?, ?it/s]

Preparing dataset:   0%|          | 0/1000 [00:00<?, ?it/s]

Preparing dataset:   0%|          | 0/1000 [00:00<?, ?it/s]

5000


In [8]:
print(len(images_list))

998


In [13]:

from tqdm.notebook import tqdm
import numpy as np
from PIL import Image
import matplotlib.pyplot as plt
import math
from math import ceil

eps_range = [0.1, 0.2, 0.3]
max_iter_range = [2]
attack_name = 'DeepFool_v3'

images_list_max_iter = []
max_iter_range_len = len(max_iter_range)
offset_max_iter = len(images_list)//max_iter_range_len

for jjeee in range(max_iter_range_len):
  if len(images_list) - (jjeee*offset_max_iter+offset_max_iter) < offset_max_iter:
    end_slice = len(images_list)
  else:
    end_slice = jjeee*offset_max_iter+offset_max_iter
  images_list_max_iter.append(images_list[jjeee*offset_max_iter:end_slice])


for jjeee in range(max_iter_range_len):
  batch_size = len(images_list_max_iter[jjeee]) // len(eps_range)

  for batch_idx in range(0, len(images_list_max_iter[jjeee])-1, batch_size):

      # Determine epsilon index for this batch
      
      eps_index = batch_idx // batch_size
      if eps_index >= len(eps_range):
         # skip
          continue
      current_eps = eps_range[eps_index]

      # Set epsilon for the attacker
      attack = DeepFool(classifier=classifier, epsilon=current_eps, max_iter=max_iter_range[jjeee], verbose=False)

      for idx in tqdm(range(batch_idx, min(batch_idx + batch_size, len(images_list))), desc=f'Processing DF untargeted with eps: {current_eps}'):
          img = images_list[idx]
          img = np.expand_dims(img, axis=0)
          x_train_adv = attack.generate(img)
          x_train_adv = x_train_adv.squeeze(0)
          x_train_adv = (x_train_adv*255.0).astype(np.uint8)

          # # Create PIL image
          image = Image.fromarray(np.transpose(x_train_adv, (1, 2, 0)))

          # # Plot dell'immagine
          # plt.imshow(image)
          # plt.axis('off')  # Rimuove gli assi del plot

          # # Mostra il plot
          # plt.show()

          # Crea la directory se non esiste
          directory = f"face_dataset/adversarial_samples/{attack_name}"
          if not os.path.exists(directory):
            os.makedirs(directory)

          # Save the image
          image.save(f"face_dataset/adversarial_samples/{attack_name}/image_max_iter_{max_iter_range[jjeee]}_eps_{current_eps}_{idx}.jpg")

print("Adversarial images generation with DeepFool completed.")

Processing DF untargeted with eps: 0.1:   0%|          | 0/332 [00:00<?, ?it/s]

Processing DF untargeted with eps: 0.2:   0%|          | 0/332 [00:00<?, ?it/s]

Processing DF untargeted with eps: 0.3:   0%|          | 0/332 [00:00<?, ?it/s]

Adversarial images generation with DeepFool completed.


## CW

In [17]:
from art.attacks.evasion import CarliniL2Method

In [18]:
images_list = []
for idx in tqdm(sample_for_attack['bim']['targeted'], desc="Preparing dataset"):
    image = np.transpose(image_files[idx], (2, 0, 1))
    image = image / 255.0
    image = image.astype(np.float32)
    images_list.append(image)

for idx in tqdm(sample_for_attack['fgsm']['untargeted'], desc="Preparing dataset"):
    image = np.transpose(image_files[idx], (2, 0, 1))
    image = image / 255.0
    image = image.astype(np.float32)
    images_list.append(image)
for idx in tqdm(sample_for_attack['fgsm']['targeted'], desc="Preparing dataset"):
    image = np.transpose(image_files[idx], (2, 0, 1))
    image = image / 255.0
    image = image.astype(np.float32)
    images_list.append(image)
print(len(images_list))

Preparing dataset:   0%|          | 0/1000 [00:00<?, ?it/s]

Preparing dataset:   0%|          | 0/1000 [00:00<?, ?it/s]

Preparing dataset:   0%|          | 0/1000 [00:00<?, ?it/s]

3000


### Untargeted

In [39]:
# from tqdm import tqdm
# images_list = []
# for idx in tqdm(sample_for_attack['cw']['untargeted'], desc="Preparing dataset"):
#     image = np.transpose(image_files[idx], (2, 0, 1))
#     image = image / 255.0
#     image = image.astype(np.float32)
#     images_list.append(image)

Preparing dataset: 100%|██████████| 1000/1000 [00:00<00:00, 4520.73it/s]


In [19]:
from tqdm import tqdm
import numpy as np
from PIL import Image
import matplotlib.pyplot as plt
import math
from math import ceil

binary_search_steps = 1
confidence = 0.5
max_iter = 5
learning_rate = 0.01
initial_const = 1000
targeted = False
cw_untargeted_attacker = CarliniL2Method(classifier=classifier, binary_search_steps=binary_search_steps,
                          confidence=confidence, max_iter=max_iter, learning_rate=learning_rate,
                          initial_const=initial_const, targeted=targeted, verbose=False)

bss_range = [6,8]
max_iter_range = [5]
attack_name = 'CW_untargeted_v2'

images_list_max_iter = []
max_iter_range_len = len(max_iter_range)
offset_max_iter = len(images_list)//max_iter_range_len

for jjeee in range(max_iter_range_len):
  if len(images_list) - (jjeee*offset_max_iter+offset_max_iter) < offset_max_iter:
    end_slice = len(images_list)
  else:
    end_slice = jjeee*offset_max_iter+offset_max_iter
  images_list_max_iter.append(images_list[jjeee*offset_max_iter:end_slice])


for jjeee in range(max_iter_range_len):
  batch_size = ceil(len(images_list_max_iter[jjeee]) / len(bss_range))

  for batch_idx in range(0, len(images_list_max_iter[jjeee])-1, batch_size):

      # Determine epsilon index for this batch
      bss_index = batch_idx // batch_size
      current_bss = bss_range[bss_index]

      # Set params for the attacker
      cw_untargeted_attacker = CarliniL2Method(classifier=classifier, binary_search_steps=current_bss,
                          confidence=confidence, max_iter=max_iter_range[jjeee], learning_rate=learning_rate,
                          initial_const=initial_const, targeted=targeted, verbose=False)

      # print(current_bss)

      for idx in tqdm(range(batch_idx, min(batch_idx + batch_size, len(images_list))), desc=f'Processing CW untargeted with bss: {current_bss}'):
          img = images_list[idx]
          img = np.expand_dims(img, axis=0)
          x_train_adv = cw_untargeted_attacker.generate(img)

          difference = np.subtract(img, x_train_adv)
    
          

          x_train_adv = x_train_adv.squeeze(0)
          x_train_adv = (x_train_adv*255.0).astype(np.uint8)

          # # Create PIL image
          image = Image.fromarray(np.transpose(x_train_adv, (1, 2, 0)))

          # Crea la directory se non esiste
          directory = f"./face_dataset/adversarial_samples/{attack_name}"
          if not os.path.exists(directory):
            os.makedirs(directory)

          # Save the image
          image.save(f"./face_dataset/adversarial_samples/{attack_name}/image_max_iter_{max_iter_range[jjeee]}_bss_{current_bss}_{idx}.jpg")

print("\nAdversarial images generation with CW untargeted completed.")

Processing CW untargeted with bss: 8: 100%|██████████| 1500/1500 [2:24:29<00:00,  5.78s/it] 


Adversarial images generation with CW untargeted completed.


### Targeted

In [20]:
# images_list = []
# for idx in tqdm(sample_for_attack['cw']['targeted'], desc="Preparing dataset"):
#     image = np.transpose(image_files[idx], (2, 0, 1))
#     image = image / 255.0
#     image = image.astype(np.float32)
#     images_list.append(image)
images_list = []
for idx in tqdm(sample_for_attack['cw']['untargeted'], desc="Preparing dataset"):
    image = np.transpose(image_files[idx], (2, 0, 1))
    image = image / 255.0
    image = image.astype(np.float32)
    images_list.append(image)
for idx in tqdm(sample_for_attack['cw']['targeted'], desc="Preparing dataset"):
    image = np.transpose(image_files[idx], (2, 0, 1))
    image = image / 255.0
    image = image.astype(np.float32)
    images_list.append(image)

print(len(images_list))

Preparing dataset: 100%|██████████| 1000/1000 [00:00<00:00, 1170.39it/s]

2000


In [ ]:
from tqdm import tqdm
import numpy as np
from PIL import Image
import matplotlib.pyplot as plt
import math
from math import ceil
import tensorflow as tf

binary_search_steps = 1
confidence = 0.5
max_iter = 5
learning_rate = 0.01
initial_const = 1000
targeted = True

cw_targeted_attacker = CarliniL2Method(classifier=classifier, binary_search_steps=binary_search_steps,
                          confidence=confidence, max_iter=max_iter, learning_rate=learning_rate,
                          initial_const=initial_const, targeted=targeted, verbose=False)

target_class = 0
targeted_label = np.array(target_class)
one_hot_bob_targeted_label = np.expand_dims(tf.keras.utils.to_categorical(targeted_label, num_classes=nb_classes), axis=0)



bss_range = [6,8]
max_iter_range = [5]
attack_name = 'CW_targeted_v2'

images_list_max_iter = []
max_iter_range_len = len(max_iter_range)
offset_max_iter = len(images_list)//max_iter_range_len

for jjeee in range(max_iter_range_len):
  if len(images_list) - (jjeee*offset_max_iter+offset_max_iter) < offset_max_iter:
    end_slice = len(images_list)
  else:
    end_slice = jjeee*offset_max_iter+offset_max_iter
  images_list_max_iter.append(images_list[jjeee*offset_max_iter:end_slice])


for jjeee in range(max_iter_range_len):
  batch_size = ceil(len(images_list_max_iter[jjeee]) / len(bss_range))

  for batch_idx in range(0, len(images_list_max_iter[jjeee])-1, batch_size):

      # Determine epsilon index for this batch
      bss_index = batch_idx // batch_size
      current_bss = bss_range[bss_index]

      # Set epsilon for the attacker
      cw_targeted_attacker = CarliniL2Method(classifier=classifier, binary_search_steps=current_bss,
                          confidence=confidence, max_iter=max_iter_range[jjeee], learning_rate=learning_rate,
                          initial_const=initial_const, targeted=targeted, verbose=False)
      # print(current_bss)

      for idx in tqdm(range(batch_idx, min(batch_idx + batch_size, len(images_list))), desc=f'Processing CW untargeted with bss: {current_bss}'):
          img = images_list[idx]
          img = np.expand_dims(img, axis=0)
          x_train_adv = cw_targeted_attacker.generate(img, one_hot_bob_targeted_label)

          difference = np.subtract(img, x_train_adv)
    
          # Verifica se tutti i valori nella differenza sono zero
          if np.all(difference == 0):
              continue

          x_train_adv = x_train_adv.squeeze(0)
          x_train_adv = (x_train_adv*255.0).astype(np.uint8)

          # # Create PIL image
          image = Image.fromarray(np.transpose(x_train_adv, (1, 2, 0)))

          # Crea la directory se non esiste
          directory = f"./face_dataset/adversarial_samples/{attack_name}"
          if not os.path.exists(directory):
            os.makedirs(directory)

          # Save the image
          image.save(f"./face_dataset/adversarial_samples/{attack_name}/image_max_iter_{max_iter_range[jjeee]}_bss_{current_bss}_{idx}.jpg")

print("\nAdversarial images generation with CW targeted completed.")